In [1]:
%use kotlin-statistics, krangl, lets-plot, numpy(0.1.4)

@file:Repository("https://repo1.maven.org/maven2")
@file:DependsOn("de.sldk:kotbar:0.1.0")

In [2]:
enum class Kernel {
    LINEAR, POLYNOMIAL, GAUSSIAN
}

val polynomialParams = listOf(2,3,4,5)
val gaussianParams = listOf(1,2,3,4,5)
val Cbounds = listOf(0.05, 0.1, 0.5, 1.0, 5.0, 10.0, 50.0, 100.0)

fun linearKernel(a: Obj, b: Obj): Double {
    var res: Double = 0.0
    for(i in a.x.indices) {
        res += a.x[i] * b.x[i]
    }
    return res
}

fun polynomialKernel(a: Obj, b: Obj, deg: Int): Double {
    var res: Double = 0.0
    for(i in a.x.indices) {
        res += (a.x[i] * b.x[i]).pow(deg)
    }
    return res
}

fun gaussianKernel(a: Obj, b: Obj, par: Int): Double {
    var res: Double = 0.0
    for(i in a.x.indices) {
        res += abs(a.x[i] - b.x[i])
    }
    return E.pow(-par * res.pow(2))
}

class Obj(
    var x: MutableList<Double>,
    var y: Int
) {
    override fun toString(): String {
        return x.joinToString(" ") + " : ${y}"
    }
}

In [3]:
val CHIPS = "res/chips.csv"
val GEYSER = "res/geyser.csv"
fun readData(file: String): List<Obj> {
    val df = DataFrame.readCSV(file)
    val X = df.remove("class").toDoubleMatrix()
    val Y = df.get("class").values().map{ it as String}.map {
        if (it == "P") 1
        else -1
    }
    val objs = ArrayList<Obj>()
    for(i in X[0].indices) {
        val x = ArrayList<Double>()
        for (j in X.indices) {
            x.add(X[j][i])
        }
        objs.add(Obj(x,Y[i]))
    }
    normilize(objs)
    return objs
}

 fun normilize(objs: List<Obj>) {
        for(i in 0 until objs[0].x.size) {
            var min = Double.MAX_VALUE
            var max = Double.MIN_VALUE
            for (obj in objs) {
                if (obj.x[i] < min) {
                    min = obj.x[i]
                }
                if (obj.x[i] > max) {
                    max = obj.x[i]
                }
            }
            val b = max - min
            for (obj in objs) {
                obj.x[i] = if (b == 0.0) {
                    0.0
                } else {
                    (obj.x[i] - min) / b
                }
            }
        }
    }


readData(CHIPS).joinToString("\n")

0.46362488624228676 0.7821083336882001 : 1
0.3878693509103247 0.7743261082485202 : 1
0.32423446977069603 0.7782172209683602 : 1
0.2393883122826767 0.6770482902525231 : 1
0.16666228293976232 0.6575927266533237 : 1
0.1606022188672099 0.5214091044585445 : 1
0.22726818413757185 0.4280208022825022 : 1
0.2757486967179913 0.30739790486735086 : 1
0.44544364193017244 0.1945556359919942 : 1
0.5060469128918393 0.13618894519439598 : 1
0.6393788434325633 0.10895115615551675 : 1
0.7151349048117539 0.13229783247455607 : 1
0.7727055135010021 0.28016011582847167 : 1
0.8242213185899829 0.31128901758719074 : 1
0.7242250009205826 0.6692660648128433 : 1
0.6060432305612398 0.7198505301707618 : 1
0.5242271051094967 0.6965038538517225 : 1
0.41211118534222 0.8443661372056381 : 1
0.34544469402462946 0.7821083336882001 : 1
0.1848424751574196 0.7470883192096409 : 1
0.11818177035934284 0.7276327556104416 : 1
0.10605638174195277 0.5875526976962059 : 1
0.12424183443189526 0.41245635140314274 : 1
0.21514805599246697 

In [4]:
fun calcF(kernelDist: DoubleArray, param: MutableList<Double>, target: List<Int>, b: Double): Double {
    var res = 0.0
    for (i in 0 until target.size) {
        res += param[i] * kernelDist[i] * target[i]
    }
    return res + b
}
 
fun calcKernel(a: Obj, b: Obj, par: Int, kernel: Kernel): Double {
    return when(kernel){
        Kernel.LINEAR -> linearKernel(a,b)
        Kernel.POLYNOMIAL -> polynomialKernel(a,b,par)
        Kernel.GAUSSIAN -> gaussianKernel(a,b,par)
    }
}


val tau = 1e-6
val eps = 1e-6
fun smo(objs: List<Obj>, kernelType: Kernel, par: Int, C: Double): Pair<List<Double>, Double> {
    val N = objs.size
    val target = objs.map {it.y}.toList()
    val lambda = DoubleArray(N).toMutableList()
    var b = 0.0
    val kernel = Array<DoubleArray>(N) {DoubleArray(N)}
    for(i in 0 until N) {
        for (j in 0 until N) {
            kernel[i][j] = calcKernel(objs[i], objs[j], par, kernelType)
        }
    }
    var js = (0 until N).toList()
    val startTime = System.currentTimeMillis()
    for (a in 1..1500) {
//     while (System.currentTimeMillis() - startTime < 1200) {
        js = js.shuffled()
        for (i in 0 until N) {
            // calc i-th object error
            val Ri = calcF(kernel[i], lambda, target, b) - target[i]
            if ((target[i] * Ri < -tau && lambda[i] < C) || (target[i] * Ri > tau && lambda[i] > 0)) {
                // pick pair
                val j = js[i]
                if (i == j) continue
                // calc j-th object error
                val Rj = calcF(kernel[j], lambda, target, b) - target[j]
                // calc L, H
                var L: Double
                var H: Double
                if (target[i] == target[j]) {
                    val g = lambda[i] + lambda[j]
                    if (g > C) {
                        L = g - C.toDouble()
                        H = C.toDouble()
                    } else {
                        L = 0.0
                        H = g
                    }
                } else {
                    val g = lambda[i] - lambda[j]
                    if (g > 0.0) {
                        L = 0.0
                        H = C.toDouble() - g
                    } else {
                        L = -g
                        H = C.toDouble()
                    }
                }
                if (L == H) {
                    continue
                }
                val nu: Double = 2.0 * kernel[i][j] - kernel[i][i].toDouble() - kernel[j][j].toDouble()
                // calc new lambda[j]
                var lambdaJ2: Double
                if (nu < -eps) {
                    val lambdaJ1 = lambda[j] - target[j] * (Ri - Rj) / nu
                    lambdaJ2 = if (lambdaJ1 >= H) {
                        H
                    } else if (lambdaJ1 > L && lambdaJ1 < H) {
                        lambdaJ1
                    } else {
                        L
                    }
                } else {
                    continue
                }
                if (abs(lambdaJ2 - lambda[j]) < eps) {
                    continue
                }
                // calc new lambda[i]
                val s = target[i] * target[j].toDouble()
                val lambdaI1 = lambda[i] - s * (lambdaJ2 - lambda[j])
                var lambdaI2: Double
                lambdaI2 = lambdaI1
                // calc new w0 = b
                val b1 = b - Ri - target[i] * (lambdaI2 - lambda[i]) * kernel[i][i] -
                        target[j] * (lambdaJ2 - lambda[j]) * kernel[i][j]
                val b2 = b - Rj - target[i] * (lambdaI2 - lambda[i]) * kernel[i][j] -
                        target[j] * (lambdaJ2 - lambda[j]) * kernel[j][j]
                val b3 = (b1 + b2) / 2.0
                b = if (lambda[i] > 0.0 && lambda[i] < C) {
                    b1
                } else if (lambda[j] > 0.0 && lambda[j] < C) {
                    b2
                } else {
                    b3
                }

                lambda[i] = lambdaI2
                lambda[j] = lambdaJ2

            }
        }
    }
    return Pair(lambda, b)
}

In [5]:
class ConfInfo(
        var tp: Int = 0,
        var fp: Int = 0,
        var fn: Int = 0,
        var tn: Int = 0,
        var cnt: Int = 0,
        var prec: Double = 0.0,
        var recall: Double = 0.0,
        var fSc: Double = 0.0
 )

fun predict(x: Obj, lambda: List<Double>, b: Double, objs: List<Obj>, kernelType: Kernel, kernelPar: Int): Int {
    var res = 0.0
    for (i in 0 until objs.size) {
        res += lambda[i] * calcKernel(x, objs[i], kernelPar, kernelType) * objs[i].y
    }
    res += b
    return if (res >= 0.0) 1 else -1
}

fun splitIntoBatches(objs: List<Obj>, num: Int): List<List<Obj>> {
    val shuffledObjs = objs.shuffled()
    return shuffledObjs.chunked(objs.size / num)
}

fun getAccuracy(confMatrix: Array<IntArray>): Double {
    val k = confMatrix.size
    val infos = Array(k) { ConfInfo() }
    var all = 0
    for (i in 0 until k) {
        for (j in 0 until k) {
            val cur = confMatrix[i][j]
            all += cur
            infos[i].cnt += cur
            if (i == j) {
                infos[i].tp = cur
            } else {
                infos[i].fp += cur
                infos[j].fn += cur
            }
        }
    }
    infos.forEach {
        it.tn = all - it.fp - it.fn - it.tp
        it.recall = if (it.tp + it.fn != 0) it.tp.toDouble() / (it.tp + it.fn) else 0.0
        it.prec = if (it.tp + it.fp != 0) it.tp.toDouble() / (it.tp + it.fp) else 0.0
        it.fSc = if (it.recall + it.prec != 0.0) 2 * it.recall * it.prec / (it.recall + it.prec) else 0.0
    }
    return (infos.map{it.tn}.sum() + infos.map{it.tp}.sum()).toDouble() / 
    (infos.map {it.tp + it.fn}.sum() + infos.map {it.fp + it.tn}.sum())
}

fun getBestSMO(file: String, kernelType: Kernel) {
    val objs = readData(file)
    var bestAcc = 0.0
    var bestKernelParam: Int = 0
    var bestC: Double = 0.0
    val params = when (kernelType) {
        Kernel.LINEAR -> listOf(0)
        Kernel.POLYNOMIAL -> polynomialParams
        Kernel.GAUSSIAN -> gaussianParams
    }
    for (par in params) {
        for (c in Cbounds) {
            val batches = splitIntoBatches(objs, 5)
            val confMatrix = Array(2) {IntArray(2)}
            for((i, testSet) in batches.withIndex()) {
                val trainSet = batches.filterIndexed {j, _ -> j != i}.flatMap{it}
                val (lambda, b) = smo(trainSet, kernelType, par, c)
                val testRes = testSet.map {
                    predict(it, lambda, b, trainSet, kernelType, par)
                }
                for (j in testSet.indices) {
                    val testR = if (testRes[j] == -1) 0 else 1
                    val testS = if (testSet[j].y == -1) 0 else 1
                    confMatrix[testR][testS] += 1

                }
            }
            val acc = getAccuracy(confMatrix)
            if (acc > bestAcc) {
                bestAcc = acc
                bestKernelParam = par
                bestC = c
            }

        }
    }
    println(""" for ${file} and kernel = ${kernelType} best params:
    accuracy = ${bestAcc}
    kernel param = ${bestKernelParam}
    C param = ${bestC}
    """)
    buildPlot(objs, kernelType, bestKernelParam, bestC)
}

fun buildPlot(objs: List<Obj>, kernelType: Kernel, par: Int, c: Double) {
    val (lambda, b) = smo(objs, kernelType, par, c)
    val testRes = objs.map {
        predict(it, lambda, b, objs, kernelType, par)
    }
    val trainX0 = ArrayList<Double>()
    val trainX1 = ArrayList<Double>()
    val trainY = ArrayList<String>()
    for ((i, obj) in objs.withIndex()) {
        trainX0.add(obj.x[0])
        trainX1.add(obj.x[1])
        if (obj.y == 1  && testRes[i] == 1) {
            trainY.add("P")
        } else if (obj.y == 1 && testRes[i] != 1) {
            trainY.add("WP")
        } else if (obj.y == -1 && testRes[i] == -1) {
            trainY.add("N")
        } else {
            trainY.add("WN")
        }
        //println(trainY.last())
    }
    val grid = meshgrid(array<Double>(objs.map{it.x[0]}), array<Double>(objs.map{it.x[1]}))
    val X0min = objs.map{it.x[0]}.min()!!
    val X0max = objs.map{it.x[0]}.max()!!
    val X1min = objs.map{it.x[1]}.min()!!
    val X1max = objs.map{it.x[1]}.max()!!
    val X0range = X0max - X0min
    val X1range = X1max - X1min
    val X = ArrayList<Double>()
    val Y = ArrayList<Double>()
    val Z = ArrayList<Int>()
    for (i in 0..150) {
        for (j in 0..150) {
            val x = X0min + i.toDouble()*(X0range/150)
            val y = X1min + j.toDouble()*(X1range/150)
            X.add(x)
            Y.add(y)
            Z.add(predict(Obj(mutableListOf(x,y),0), lambda, b, objs, kernelType, par))
        }
    }
    //val Z = X.zip(Y).map {predict(Obj(mutableListOf(it.first,it.second),0), lambda, b, objs, kernelType, par)}
    val plotData = mapOf<String, Any>(
        "x0" to trainX0,
        "x1" to trainX1,
        "cond" to trainY
    )
    var p = lets_plot() + ggsize(500,500)
    p += geom_tile(){x=X; y=Y; fill=Z}
    p += geom_point(size = 3) { x = plotData["x0"]; y = plotData["x1"]; color = plotData["cond"]; shape = plotData["cond"]}
    p += scale_shape_manual(values = listOf(5,9,1,10))
    p.show()
}

In [6]:
getBestSMO(CHIPS, Kernel.LINEAR)

 for res/chips.csv and kernel = LINEAR best params:
    accuracy = 0.5338983050847458
    kernel param = 0
    C param = 50.0
    


In [7]:
getBestSMO(CHIPS, Kernel.POLYNOMIAL)

 for res/chips.csv and kernel = POLYNOMIAL best params:
    accuracy = 0.6779661016949152
    kernel param = 5
    C param = 10.0
    


In [12]:
getBestSMO(CHIPS, Kernel.GAUSSIAN)

 for res/chips.csv and kernel = GAUSSIAN best params:
    accuracy = 0.7966101694915254
    kernel param = 5
    C param = 1.0
    


In [9]:
getBestSMO(GEYSER, Kernel.LINEAR)

 for res/geyser.csv and kernel = LINEAR best params:
    accuracy = 0.9054054054054054
    kernel param = 0
    C param = 5.0
    


In [10]:
getBestSMO(GEYSER, Kernel.POLYNOMIAL)

 for res/geyser.csv and kernel = POLYNOMIAL best params:
    accuracy = 0.9054054054054054
    kernel param = 2
    C param = 5.0
    


In [11]:
getBestSMO(GEYSER, Kernel.GAUSSIAN)

 for res/geyser.csv and kernel = GAUSSIAN best params:
    accuracy = 0.8963963963963963
    kernel param = 1
    C param = 0.1
    
